In [6]:
import urllib.request
import zipfile
import os
import ssl


import warnings
warnings.filterwarnings('ignore')


try:
    os.mkdir("files")
except:
    pass

ssl._create_default_https_context = ssl._create_unverified_context

with urllib.request.urlopen('https://courses.cs.tau.ac.il/pyProg/2526a/resources/notebook_resources.zip') as f:
    content = f.read()

with open('files/notebook_resources.zip', 'wb') as f:
    f.write(content)

with zipfile.ZipFile('files/notebook_resources.zip', 'r') as zip_ref:
    zip_ref.extractall('files')

print(os.listdir('files'))

['baby.png', 'countries-of-the-world.csv', 'dialation.png', 'dialation_2.png', 'dog.png', 'dog_noised.png', 'erosion.png', 'erosion_2.png', 'evil_morty_1.png', 'evil_morty_change.png', 'evil_morty_change_3.png', 'evil_morty_change_noised.png', 'evil_morty_segmentation.png', 'ex1.csv', 'ex2.csv', 'foods.txt', 'infile1.txt', 'infile2.txt', 'koala.png', 'monday.txt', 'notebook_resources.zip', 'orders_2_2024.csv', 'orders_3_2024.csv', 'orders_4_2024.csv', 'out.txt', 'products2.csv', 'ship.png', 'StudentsGrades.csv', 'sunday.txt', 'witcher_1.csv', 'witcher_2.csv', 'woman_noised.png', '__MACOSX']


**שימו לב**: על מנת להריץ את התאים ב-Live Code, יש לייבא תחילה את ספרית `pandas` ע"י הרצת השורת הראשונה בתא למטה.   
בנוסף, נגביל את מספר השורות והעמודות שתופענה בהדפסת הטבלאות ע"י שורות הקוד השניה והשלישית:

In [7]:
import pandas as pd
pd.options.display.max_rows=5
pd.options.display.max_columns=5

# עריכת טבלאות מתקדמת

בפרק זה נעמיק עוד את היכרותנו עם פעולות העריכה ב`pandas` ונלמד שתי טכניקות מתקדמות יותר לעבודה עם טבלאות.
הראשונה היא שימוש במיסוך (Masking), המאפשר לסנן ולעדכן נתונים בטבלה לפי תנאים מסוימים.   

לאחר מכן נכיר את המתודה החזקה `apply`, המאפשרת לבצע חישובים מורכבים או ליצור עמודות חדשות מבלי להשתמש בלולאות מפורשות, על-ידי הפעלת פונקציה על שורות או עמודות שלמות.

הפעולות להלן יודגמו טבלת הציונים `"files/StudentsGrades.csv"`:

In [8]:
inputFileName = "files/StudentsGrades.csv"
df = pd.read_csv(inputFileName)
display(df)

Name  Programming  ...  Planet Survival  Art
0    Yael           50  ...               65   91
1   Nadav           61  ...               52   88
..    ...          ...  ...              ...  ...
11    Tom           98  ...               92   80
12    Adi           76  ...               84   70

[13 rows x 8 columns]

## מיסוך (Masking) ב`pandas`

```{admonition} **העמקה:**  מה זה Masking?
:class: dropdown, note

Mask (מסכה) היא מערך בוליאני (של ערכי `True`/`False`) שמשמש כדי לבחור אילו איברים ממערך אחר (בעל אותם ממדים) ייכללו בפעולה מסוימת, ואילו יישארו מוסתרים או יתעלמו מהם.
אפשר לחשוב על המסכה כעל שכבת פילטר שמכסה חלקים מהנתונים וחושפת רק את מה שצריך, כמו מסננת או שכבת שקף עם חורים. 

לדוגמא, עבור הטבלה שלנו `df` ניתן לייצר מסיכה מאחת העמודות  (לדוגמא, `m=df["Art"]>90`)' ולבצע מיסוך `df[m]` או `df.loc[m]`.
במיסוך זה, שורות בהן `m` מכיל את הערך `True` ייכללו בחישוב, ונתעלם משורות בהן `m` מכיל את הערך `False`.

ביצוע Masking יכול לשמש אותנו כדי להחזיר תת-טבלה, או כדי לבצע פעולה על תת-טבלה.

```


כעת נבחן כמה דוגמאות לשימוש ב-Masking על `DataFrame`:

נניח כי נרצה להסיר את כל הסטודנטיות ששמן יעל.

תחילה ניצור מסיכה:

In [134]:
msk=df['Name'] != 'Yael'
display(msk)

0     False
1      True
      ...  
11     True
12     True
Name: Name, Length: 13, dtype: bool

ולאחר מכן נסנן את הטבלה:

In [133]:
display(df[msk])

Name  Programming  Marine Biology  Stellar Cartography  Math  History  \
0     Yael           50              56                   70    60       87   
2   Michal           81              72                   76    94       67   
..     ...          ...             ...                  ...   ...      ...   
11     Tom           98              76                   98   100       98   
12     Adi           76              87                   34    90       88   

    Planet Survival  Art  
0                65   91  
2                81   78  
..              ...  ...  
11               92   80  
12               84   70  

[12 rows x 8 columns]

ניתן גם **להשאיר** רק סטודנטיות ששמן יעל באמצעות יצירת מסיכה של התנאי ההפוך. 

נראה כיצד לעשות זאת בשורה אחת בלבד:

In [136]:
df[df['Name'] == 'Yael']

Name  Programming  Marine Biology  Stellar Cartography  Math  History  \
0  Yael           50              56                   70    60       87   

   Planet Survival  Art  
0               65   91

בדומה לאופרטורים אריתמטיים, ניתן להפעיל פעולות `and`, `or` ו-`not` עבור סדרות וטבלאות בוליאניות (או במילים אחרות, עבור מסיכות).  
אך בשונה מערכים בוליאניים רגילים, כאן **לאופרטורים אלו יש סימון אחר**:
- `and` --> `&`
- `or` --> `|`
- `not` --> `~`

נדגים זאת באמצעות החזרת כל הסטודנטים שקיבלו מעל 70 מתמטיקה ומעל 90 באומנות:

In [148]:
display(df[(df['Math'] > 70) & (df['Art'] > 90)])

Name  Programming  Marine Biology  Stellar Cartography  Math  History  \
6  Yarden           63              62                   70    74       92   
7     Avi           78              64                   54    88       97   

   Planet Survival  Art  
6               98   94  
7               76  100

```{admonition} **שימו לב**
:class: error
ב`pandas` האופרטורים הלוגיים `&` `|` `~` קודמים להשוואתיים (כמו `<` `>` `==`). לכן חשוב לעטוף כל מסיכה בסוגריים על מנת למנוע מהאופרטור הלוגי לפעול לפני האופרטור ההשוואתי.
```

באמצעות Masking ניתן גם לבצע **השמה מותנית**, כלומר, לבצע השמה רק במקומות בהם יש במסיכה `True`.

לדוגמא, בשורה הבאה "נעביר" את כל הסטודנטים שנכשלו בתכנות, וניתן להם את הציון 60 (אתם יכולים לראות שהציון של יעל התחלף מ50 ל60).

In [11]:
df.loc[df["Programming"] < 60, "Programming"] = 60
display(df)

Name  Programming  ...  Planet Survival  Art
0    Yael           60  ...               65   91
1   Nadav           61  ...               52   88
..    ...          ...  ...              ...  ...
11    Tom           98  ...               92   80
12    Adi           76  ...               84   70

[13 rows x 8 columns]

## מתודת `apply`

המתודה `apply` מאפשרת להפעיל פונקציה על עמודה או על כל שורה ב-DataFrame. במקום להשתמש בלולאות, `apply` מאפשרת לנו לבצע חישוב או שינוי על כל השורות או העמודות של הטבלה בבת אחת.   
באופן דומה, עבור סדרה, `apply` תבצע את הפעולה על כל ערכים בסדרה **בבת אחת**.   

לדוגמא, אם נרצה להעלות את כל הציונים בעמודה `Art` ב10, אבל לוודא שלא יהיו ציונים גבוהים מ100, נוכל לעשות זאת באופן הבא:


In [14]:
df["Art"]=df["Art"].apply(lambda a: min(100, a+10))

display(df)

Name  Programming  ...  Planet Survival  Art
0    Yael           60  ...               65  100
1   Nadav           61  ...               52   98
..    ...          ...  ...              ...  ...
11    Tom           98  ...               92   90
12    Adi           76  ...               84   80

[13 rows x 8 columns]

בדומה לחישוב ממוצע המקצועות שראינו קודם, גם ל`apply`, יש פרמטר בשם `axis`:  
בברירת מחדל, `apply` מופעל עם הקלט `axis=0`. כלומר, מתבצעת פעולה **בין השורות השונות**, או במילים אחרות - **על כל עמודה בנפרד**.
ולהיפך, הפעלת `apply` עם `axis=1` תבצע פעולה **בין העמודות השונות**, או במילים אחרות - **על כל שורה בנפרד**.  



נדגים זאת באמצעות ממוצע באמצעות `apply`:   

In [17]:
display(df.iloc[:,1:].apply(lambda a: a.mean(), axis=1))

0     71.142857
1     71.571429
        ...    
11    93.142857
12    77.000000
Length: 13, dtype: float64

שימו לב ש`apply` מחלץ ממוצע עבור **כל סטודנט בנפרד** (כלומר, עבור כל שורה), והתוצאה היא **סדרה במבנה על עמודה בטבלה**, בה קיים ממוצע כל סטודנט.

מה היה קורה אם היינו מפעילים את אותה השורה עם `axis=0`?

היינו מחלצים ממוצע עבור כל **מקצוע** בנפרד (כלומר, עבור כל טור), מה שהיה מסתכם לכדי שורה חדשה (ללא עמודת שם הסטודנט, אותה חתכנו באמצעות `iloc`). 

נחזור למשימת הוספת פקטור של 10 נקודות. מה אם במקום להוסיף זאת רק עבור אומנות, היינו מוסיפים זאת **לכלל המקצועות**?   
היינו חושבים אולי לבצע משהו כזה:

``` python
(df.iloc[:,1:]=df.iloc[:,1:].apply(lambda a: min(100, a+10)
```

אבל מכיוון שאנו פועלים כעת על טבלה (ולא על סדרה כמו בדוגמא הראשונה), `a` בפונקציית ה`lambda` ייצג שורה שלמה. כלומר פעולת המינימום לא תתבצע עבור כל תא בנפרד, כפי שהיינו רוצים.

לכן, נעזר במתודה `clip` של `pandas` המאפשרת לקטום ערכים בכל תא בנפרד. במקרה שלנו, היינו צריכים להגביל את הערכים רק מלמעלה, ולכן נשתמש בפרמטר `upper=100`. 

כעת המימוש יראה כך:


In [160]:
df.iloc[:,1:].apply(lambda a: a+10).clip(upper=100)

Programming  Marine Biology  Stellar Cartography  Math  History  \
0            70              66                   80    70       97   
1            71              87                   85    85       73   
..          ...             ...                  ...   ...      ...   
11          100              86                  100   100      100   
12           86              97                   44   100       98   

    Planet Survival  Art  
0                75  100  
1                62   98  
..              ...  ...  
11              100   90  
12               94   80  

[13 rows x 7 columns]


```{admonition} **הערה**
:class: info


במקרה הזה, אין חשיבות לפרמטר `axis` ב`apply` מכיוון שהפעולה נעשית בסופו של דבר על כל ערך בנפרד, והם אינם "נסכמים" ביחד.

```


#### תרגיל

בשורה אחת בלבד, שנו באמצעות המתודה `apply` את שמות הסטודנטים כך שכולם יהיו באותיות גדולות.

In [ ]:
# Write your code here
display(df)